# Class-Dependent Perturbation Effects in Evaluating Time Series Attributions

This notebook demonstrates the implementation and analysis of class-dependent effects in perturbation-based evaluation of feature attributions for time series classification, as presented in our paper "Class-Dependent Perturbation Effects in Evaluating Time Series Attributions."

## Overview

Our research examines how perturbation-based evaluation of feature attributions can exhibit varying effectiveness across different predicted classes. These class-dependent effects have important implications for XAI evaluation methodology, particularly when assessing attribution methods using perturbation analysis.

The notebook is organized into two main sections:

### Example Functionality
This section provides practical demonstrations of the key methods employed in our research:
- Loading and preprocessing univariate time series data from the UCR repository
- Training time series classifiers and loading pre-trained models
- Generating feature attributions using various methods (Gradients, Integrated Gradients, SmoothGrad, Gradient SHAP, and Feature Occlusion)
- Using perturbation strategies for attribution evaluation
- Calculating degradation scores (DS)

These examples help build intuition about the building blocks of the methodological approach and the experimental framework used in our investigation of class-dependent perturbation effects.

### Paper Experiment Results
This section demonstrates how to load experimental results from CSV files and reproduce the visualizations presented in the paper.

# Imports

In [1]:
%load_ext autoreload
%autoreload 2

In [ ]:
import logging
import os
from pathlib import Path

import numpy as np
import pandas as pd
import torch
from lets_plot import LetsPlot, element_rect, ggsize, labs, theme

from tsxai.attribution.evaluation.metrics import (
    PerturbationResult,
    calculate_class_adjusted_metric,
    plot_perturbation_analysis_curves,
)
from tsxai.attribution.explainer import TimeSeriesExplainer
from tsxai.data.dataloaders import prepare_dataloaders
from tsxai.data.loading import load_ucr_data, print_dataset_info
from tsxai.modelling.evaluation import evaluate_model
from tsxai.modelling.models import InceptionTime, ResNet
from tsxai.modelling.training import setup_deterministic_training, train_model
from tsxai.modelling.utils import load_trained_model
from tsxai.utils.logging import setup_logger
from tsxai.utils.results import load_and_format_experiment_results
from tsxai.visualization.utils import get_plot_dimensions, theme_paper
from tsxai.visualization.visualize import (
    plot_confusion_matrix,
    plot_metric_distributions,
    plot_parallel_coords,
    plot_perturbation_analysis,
    vis_time_series_classification_samples,
)

2025-03-31 14:16:39.706284: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2025-03-31 14:16:39.718900: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:467] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1743423399.733680 1126756 cuda_dnn.cc:8579] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1743423399.738131 1126756 cuda_blas.cc:1407] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
W0000 00:00:1743423399.748939 1126756 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking 

2025-03-31 14:16:46.334 |     INFO |        training | Enabled Tensor Cores with medium precision


In [3]:
while "notebooks" in os.getcwd():
    os.chdir(Path.cwd().parent)
print(f"Working directory: {os.getcwd()}")

Working directory: /home/gbaer/code/class-perturbation-effects


In [4]:
## Miscellaneous settings & setup
USE_CUDA = True  # Set to False to use CPU for training and inference

logger = setup_logger(__name__, logging.INFO)
LetsPlot.setup_html(no_js=True)
width, height = get_plot_dimensions(scale=2)

device = torch.device("cuda" if USE_CUDA and torch.cuda.is_available() else "cpu")
logger.info(f"Using device: {device}")

2025-03-31 14:16:46.503 |     INFO |       815250717 | Using device: cuda


# Example functionality
## Data
First, we import the data from the UCR time series archive. We will use the `"Wafer"` dataset for demonstration here, but you can choose to load any other dataset available. 

`data` will be a custom `UCRDataset` dataclass, containing `X_train`, `X_test`, `y_test`, `y_train`, `n_classes`, `n_features`, `n_timesteps` and more.

We also print some metadata of the dataset, to get an idea of the number of train and test samples, class distributions, etc. And plot 5 samples for each class, to get an idea of the shape of the univariate time series.

In [5]:
dataset_name: str = "Wafer"
n_samples_to_vis: int = 5

data = load_ucr_data(dataset_name, remap_labels_ascending=True, on_disk=False)

# Show dataset metadata and plot some samples
print_dataset_info(data)
ts_samples_plot = vis_time_series_classification_samples(
    data.to_plotting_df(split="train"), n_samples_per_label=n_samples_to_vis, n_col=2
)
ts_samples_plot.show()

2025-03-31 14:16:46.568 |     INFO |         loading | Loading UCR dataset: Wafer
2025-03-31 14:16:46.578 |     INFO |         loading | Dataset loaded: train=1000 test=6164 samples
2025-03-31 14:16:46.583 |     INFO |         loading | Found 2 unique classes
2025-03-31 14:16:46.585 |     INFO |         loading | Successfully processed Wafer data: 1 features, 152 timesteps
╒═══════════════╤═════════╕
│ Metric        │   Value │
╞═══════════════╪═════════╡
│ Train samples │    1000 │
├───────────────┼─────────┤
│ Test samples  │    6164 │
├───────────────┼─────────┤
│ Num features  │       1 │
├───────────────┼─────────┤
│ Num classes   │       2 │
├───────────────┼─────────┤
│ Num timesteps │     152 │
╘═══════════════╧═════════╛

Class Distribution:
╒═════════╤═════════╤════════╕
│ Class   │ Train   │ Test   │
╞═════════╪═════════╪════════╡
│ Class 0 │ 9.7%    │ 10.8%  │
├─────────┼─────────┼────────┤
│ Class 1 │ 90.3%   │ 89.2%  │
╘═════════╧═════════╧════════╛


<path d="M18.34267223132107 257.1573566263537 L18.34267223132107 257.1573566263537 L20.772165242092072 260.3883424184216 L23.201658252863076 259.18299589859396 L25.63115126363408 259.86010656858434 L28.06064427440508 259.43851258008783 L30.490137285176083 259.7055327342531 L32.91963029594709 259.5360736774276 L35.349123306718084 259.6510506608262 L37.778616317489096 259.6112454318421 L40.20810932826009 259.60826035349066 L42.6376023390311 259.6492330016786 L45.0670953498021 259.5423965704706 L47.4965883605731 259.7114376159037 L49.92608137134411 259.48299501762426 L52.35557438211511 259.845861543718 L54.785067392886106 259.2618469064349 L57.21456040365712 260.0704428715984 L59.644053414428114 234.73388206666633 L62.073546425199126 209.73741746454965 L64.50303943597012 211.15656488631893 L66.93253244674112 215.0396497057563 L69.36202545751213 218.29181599699317 L71.79151846828313 219.25028097156724 L74.22101147905413 221.34054631141362 L76.65050448982514 220.7909604983294 L79.07999750059614 223.63148850182893 L81.50949051136715 220.28619479564813 L83.93898352213814 231.57489497106388 L86.36847653290914 262.42496421820465 L88.79796954368015 258.16317739605313 L91.22746255445115 260.4832397915133 L93.65695556522216 259.07134166641333 L96.08644857599316 259.9740793204097 L98.51594158676416 259.40643742363875 L100.94543459753517 259.7330235735704 L103.37492760830617 259.606746474394 L105.80442061907718 259.6246519233448 L108.23391362984817 259.6764024868925 L110.66340664061917 259.5284917290497 L113.09289965139018 259.89337676060563 L115.52239266216118 257.9018035339084 L117.95188567293218 235.28872785643773 L120.38137868370319 218.97420390390087 L122.81087169447419 217.5118669927457 L125.24036470524518 217.5664432128826 L127.6698577160162 217.48875585837717 L130.09935072678718 217.48590509599865 L132.5288437375582 217.4526976684507 L134.9583367483292 217.493151882089 L137.38782975910019 217.37179928348985 L139.8173227698712 217.20809447357897 L142.2468157806422 217.31164079109521 L144.67630879141322 217.26818769092134 L147.1058018021842 217.2137031069155 L149.53529481295521 217.2220206549208 L151.96478782372623 217.197663018112 L154.3942808344972 217.0976465745757 L156.82377384526822 217.12704545388212 L159.25326685603923 217.1615382978438 L161.68275986681024 217.1480087879734 L164.11225287758123 217.15667028529256 L166.54174588835224 217.1381447233453 L168.97123889912325 217.1072169014686 L171.40073190989423 217.14263865963554 L173.83022492066524 217.10805292425331 L176.25971793143626 217.12171549480718 L178.68921094220724 217.09112660108644 L181.11870395297825 217.15390613788722 L183.54819696374926 217.25648588251423 L185.97768997452025 217.2005778002533 L188.40718298529126 217.22581162910978 L190.83667599606227 217.212558282922 L193.26616900683328 217.25307149516522 L195.69566201760426 217.21412990533412 L198.12515502837527 217.22557563469007 L200.5546480391463 217.19100245220253 L202.98414104991727 217.1310197003332 L205.41363406068828 217.1175504443572 L207.8431270714593 217.11188657828416 L210.27262008223028 217.13824514650264 L212.7021130930013 217.11716883635935 L215.1316061037723 217.0935267145465 L217.56109911454328 217.06438893544907 L219.9905921253143 217.14809414765713 L222.4200851360853 217.15941183748748 L224.8495781468563 217.13153185843555 L227.2790711576273 217.08817667084008 L229.7085641683983 217.09082282103554 L232.1380571791693 217.09477698285517 L234.5675501899403 217.0524335585697 L236.99704320071132 217.03217569715864 L239.42653621148233 217.01032361812506 L241.8560292222533 216.9703627332471 L244.28552223302432 216.95805085415924 L246.71501524379534 216.96589892390406 L249.14450825456632 216.967327443317 L251.57400126533733 216.98420857606308 L254.00349427610834 217.01204838585207 L256.4329872868793 217.1932393780319 L258.86248029765034 217.02444311404474 L261.29197330842135 217.2861508831876 L263.7214663191923 216.79480045903526 L266.1509593299633 217.56347696387317 L268.5804523407343 216.28778402234047 

## Classifiers
### Load trained model (or train from scratch)
Next, we need trained classifiers to generate predictions for our time series data. This example demonstrates loading a pre-trained ResNet model from our experimental results.

Alternative options include:
- Switching to the InceptionTime architecture by setting `model_name = "InceptionTime"`
- Training a new model from scratch by setting `load_model = False`

The code maintains consistent data preparation settings with those used in our training script (`scripts/train_models.py`), ensuring compatibility with the evaluation framework described in our paper. This consistency is important for achieving the same results.

In [6]:
# set to True to load a pre-trained model, otherwise train a new model from scratch
load_model: bool = True
dataset_name: str = "Wafer"
model_name: str = "ResNet"  # either "ResNet" or "InceptionTime"
model_dir: str = "results/models"  # Path to previously trained models


data = load_ucr_data(dataset_name, remap_labels_ascending=True, on_disk=False)

# use same settings as in scripts/train_models.py for dataloaders
train_loader, val_loader, test_loader = prepare_dataloaders(
    data, batch_size=256, val_split=0.2, seed=42
)

if load_model:
    model = load_trained_model(data, dataset_name, model_name, model_dir)
else:
    config = {
        "dataset_name": dataset_name,
        "model_dir": "models",
        "save_model": False,
        "save_hyperparameters": False,
        "show_progress": True,
        "patience": 25,
        "epochs": 500,
    }

    # initialise models
    setup_deterministic_training()
    c_in, c_out = (data.n_features, data.n_classes)
    resnet = ResNet(c_in, c_out)
    inceptiontime = InceptionTime(c_in, c_out)
    models_dict = {"ResNet": resnet, "InceptionTime": inceptiontime}

    # train selected model
    assert model_name in models_dict.keys(), (
        f"Model {model_name} not found in models_dict"
    )
    model_to_train = models_dict[model_name]

    model = train_model(
        model=model_to_train,
        train_loader=train_loader,
        val_loader=val_loader,
        config=config,
    )

2025-03-31 14:16:46.742 |     INFO |         loading | Loading UCR dataset: Wafer
2025-03-31 14:16:46.747 |     INFO |         loading | Dataset loaded: train=1000 test=6164 samples
2025-03-31 14:16:46.751 |     INFO |         loading | Found 2 unique classes
2025-03-31 14:16:46.752 |     INFO |         loading | Successfully processed Wafer data: 1 features, 152 timesteps
2025-03-31 14:16:46.753 |     INFO |     dataloaders | Preparing dataloaders (batch_size=256, val_split=0.2)
2025-03-31 14:16:46.757 |     INFO |     dataloaders | Created dataloaders - Train: 800, Val: 200, Test: 6164
2025-03-31 14:16:46.759 |     INFO |           utils | Loading trained ResNet model for dataset Wafer
2025-03-31 14:16:46.760 |     INFO |           utils | Using device cuda for loading weights
2025-03-31 14:16:47.133 |     INFO |           utils | Successfully loaded trained ResNet model for Wafer on cuda


## Classifiers
### Evaluate Model
We evaluate the loaded model's performance using standard classification metrics. The code calculates accuracy and F1 scores, while also generating a confusion matrix to visualize prediction patterns across classes. This validation step ensures that our model achieves sufficient classification capability before proceeding to attribution analysis.

For the Wafer dataset with ResNet architecture, we observe high predictive performance (Accuracy: 0.993, F1: 0.993), which match the results reported in our paper. 

In [7]:
# compute accuracy and f1 score and display confusion matrix
perf_metrics = evaluate_model(model, test_loader, device, data.n_classes, True)
print(
    f"Accuracy: {perf_metrics[0]['accuracy']:.3f} | F1: {perf_metrics[0]['f1']:.3f}",
    f"[Data: {dataset_name}, Model: {model_name}]",
)
conf_matrix_plot = plot_confusion_matrix(perf_metrics[1])
conf_matrix_plot.show()

Accuracy: 0.993 | F1: 0.993 [Data: Wafer, Model: ResNet]


625 
 
 
 
 
 
 
 3 
 
 
 
 
 
 
 40 
 
 
 
 
 
 
 5,496 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 Predicted 0 
 
 
 
 
 
 
 Predicted 1 
 
 
 
 
 
 
 
 
 Actual 0 
 
 
 
 
 
 
 Actual 1 
 
 
 
 
 
 
 
 
 
 
 
 
 Count 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 1,000 
 
 
 
 
 
 
 
 
 2,000 
 
 
 
 
 
 
 
 
 3,000 
 
 
 
 
 
 
 
 
 4,000 
 
 
 
 
 
 
 
 
 5,000

## Feature Attributions

Now we move to generating feature attributions to explain the model's classifications. This section demonstrates using our custom `TimeSeriesExplainer` class to:
1. Generate attributions for specific samples
2. Visualize attribution results 
3. Perform perturbation analysis

Our implementation builds on the [TSInterpret](https://github.com/fzi-forschungszentrum-informatik/TSInterpret) library with additional functionality for working with `UCRDataset` objects and other visualization capabilities. 

We initialize the explainer with `split="test"` to ensure we're generating explanations for previously unseen data.

In [8]:
# initialise explainer to explain test set observations on trained model
explainer = TimeSeriesExplainer(dataset=data, model=model, split="test")

### Generating Feature Attributions

To produce feature attributions, we call the explainer's `.explain()` method with three key parameters:
- `sample_index`: Specifies which instance to explain
- `method`: Indicates which attribution algorithm to apply
- `label`: Determines which class prediction to explain (can be "predicted", "true", or a specific class index)

The underlying TSInterpret implementation supports multiple attribution methods:

```python
available_attribution_methods = ["GRAD", "IG", "GS", "DL", "DLS", "SG", "SVS", "FA", "FO"]
```

These correspond to:
* Gradients (`GRAD`)
* Integrated Gradients (`IG`)
* Gradient Shap (`GS`)
* DeepLift (`DL`)
* DeepLiftShap (`DLS`)
* SmoothGrad (`SG`)
* Shapley Value Sampling(`SVS`)
* Feature Ablation (`FA`)
* Feature Occlusion (`FO`)

Note: For the analysis in our paper, we specifically focus on five methods: Gradients, Integrated Gradients, SmoothGrad, Gradient SHAP, and Feature Occlusion.

The `.explain()` method returns an `ExplanationResult` dataclass containing:
```
ExplanationResult(
    metadata=Metadata(true_label, observation_index), 
    prediction=Prediction(label, probability, all_probabilities, explained_label), 
    data=Data(ds, y, attributions, method)
)
```

This structured output provides all information needed for subsequent perturbation analysis and evaluation.

In [9]:
# Configuration for explanation
sample_idx: int = 0  # which sample to explain
method: str = "GS"  # attribution method to use
label: str | int = "predicted"  # label to explain

# explain sample
explanation = explainer.explain(sample_index=sample_idx, method=method, label=label)
print(explanation)

ExplanationResult(metadata=Metadata(true_label=1, observation_index=0), prediction=Prediction(label=1, probability=0.9961244463920593, all_probabilities=array([0.00387554, 0.99612445], dtype=float32), explained_label=1), data=Data(ds=array([  0,   1,   2,   3,   4,   5,   6,   7,   8,   9,  10,  11,  12,
        13,  14,  15,  16,  17,  18,  19,  20,  21,  22,  23,  24,  25,
        26,  27,  28,  29,  30,  31,  32,  33,  34,  35,  36,  37,  38,
        39,  40,  41,  42,  43,  44,  45,  46,  47,  48,  49,  50,  51,
        52,  53,  54,  55,  56,  57,  58,  59,  60,  61,  62,  63,  64,
        65,  66,  67,  68,  69,  70,  71,  72,  73,  74,  75,  76,  77,
        78,  79,  80,  81,  82,  83,  84,  85,  86,  87,  88,  89,  90,
        91,  92,  93,  94,  95,  96,  97,  98,  99, 100, 101, 102, 103,
       104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116,
       117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129,
       130, 131, 132, 133, 134, 135, 136, 137,

### Visualizing Feature Attributions

Our implementation includes built-in visualization capabilities through the `.visualize_attributions()` method, which provides an intuitive representation of feature importance within the time series.

The visualization consists of:
- A white line showing the original time series signal
- A heatmap overlay indicating attribution values at each time point
- A comprehensive title displaying the explained label, prediction confidence, and correctness

In this example, we visualize sample 1 using the Feature Occlusion (`FO`) method to explain the predicted label. The classifier assigns this prediction with 99.5% confidence, and the prediction matches the true label.

The resulting visualization reveals that certain constant periods at approximately time steps 0-20, 34-49, and 122-150 (where the signal remains around -1) contribute most significantly to the model's prediction. These highlighted regions align with our understanding of discriminative patterns in the Wafer dataset, where the sustained periods at specific values often characterize class membership.

In [10]:
sample_idx: int = 1
method: str = "FO"
label: str | int = "predicted"

explanation = explainer.explain(sample_index=sample_idx, method=method, label=label)
plot = explanation.visualize_attributions()
plot.show()

<path d="M2.3979759648824026 183.79974215085426 L2.3979759648824026 183.79974215085426 L7.193927894647208 183.62897710550402 L11.989879824412013 183.62897710550402 L16.78583175417682 183.62897710550402 L21.581783683941623 183.62897710550402 L26.377735613706427 183.62897710550402 L31.173687543471235 183.79974215085426 L35.96963947323604 183.62897710550402 L40.76559140300085 183.62897710550402 L45.56154333276565 183.79974215085426 L50.357495262530456 183.79974215085426 L55.15344719229526 183.79974215085426 L59.94939912206007 183.79974215085426 L64.74535105182487 183.79974215085426 L69.54130298158968 183.79974215085426 L74.33725491135448 183.79974215085426 L79.13320684111929 183.79974215085426 L83.9291587708841 183.79974215085426 L88.7251107006489 183.79974215085426 L93.52106263041371 183.79974215085426 L98.3170145601785 41.04266132263621 L103.11296648994332 8.939393939393923 L107.90891841970812 18.843588874550306 L112.70487034947293 41.04266132263621 L117.50082227923774 55.215912248723214 L122.29677420900254 68.36458926936803 L127.09272613876735 76.21964340792255 L131.88867806853213 83.90393600826809 L136.68462999829694 88.51451156847541 L141.48058192806175 92.10051497681117 L146.27653385782654 95.51575567789088 L151.07248578759135 97.56490042002665 L155.86843771735616 99.61404501603154 L160.66438964712097 172.3586805122992 L165.46034157688578 183.62897710550402 L170.25629350665056 183.62897710550402 L175.05224543641538 183.62897710550402 L179.8481973661802 183.62897710550402 L184.644149295945 183.79974215085426 L189.44010122570978 183.79974215085426 L194.2360531554746 183.62897710550402 L199.0320050852394 183.79974215085426 L203.82795701500422 183.62897710550402 L208.62390894476903 183.79974215085426 L213.4198608745338 183.79974215085426 L218.21581280429862 183.79974215085426 L223.01176473406343 183.62897710550402 L227.80771666382824 183.62897710550402 L232.60366859359306 183.79974215085426 L237.39962052335784 183.79974215085426 L242.19557245312265 68.87687505304204 L246.99152438288746 38.82275314258995 L251.78747631265227 31.821507864127398 L256.5834282424171 27.040170765711096 L261.37938017218187 25.332553045527177 L266.17533210194665 24.307976801990833 L270.9712840317115 23.79569101831683 L275.7672359614763 23.283405234642814 L280.5631878912411 22.600359081806914 L285.3591398210059 21.575787514458895 L290.1550917507707 21.405022469108673 L294.9510436805355 20.380455577948993 L299.7469956103003 20.89273668543467 L304.54294754006514 21.063501730784893 L309.3388994698299 21.063501730784893 L314.1348513995947 21.23426209994679 L318.93080332935955 21.91730825278269 L323.72675525912433 22.600359081806914 L328.52270718888917 22.600359081806914 L333.31865911865395 23.283405234642814 L338.11461104841874 23.79569101831683 L342.9105629781836 24.307976801990833 L347.70651490794836 24.649502216502952 L352.5024668377132 24.820267261853175 L357.298418767478 25.161788000176955 L362.09437069724277 25.332553045527177 L366.8903226270076 25.503313414689075 L371.6862745567724 25.844838829201194 L376.4822264865372 26.357124612875197 L381.278178416302 26.698650027387316 L386.0741303460668 26.698650027387316 L390.87008227583163 26.357124612875197 L395.6660342055964 26.527884982037094 L400.4619861353612 26.357124612875197 L405.25793806512604 26.698650027387316 L410.0538899948908 26.357124612875197 L414.84984192465566 26.698650027387316 L419.64579385442045 26.698650027387316 L424.44174578418523 26.357124612875197 L429.23769771395007 26.015599198363077 L434.03364964371485 26.527884982037094 L438.8296015734797 26.015599198363077 L443.6255535032445 26.357124612875197 L448.42150543300926 25.67407378385097 L453.2174573627741 25.844838829201194 L458.0134092925389 25.503313414689075 L462.8093612223037 25.503313414689075 L467.6053131520685 25.332553045527177 L472.4012650818333 24.478741847341055 L477.1972170115981 21.746547883620792 L481.9931689413629 17.64826161422873 L486.7891208711277 12.525403777488634 L491.58507280089253 12.696159470462206 L496.38102473

### Evaluating attributions with perturbations

To assess attribution quality, we can measure how perturbing input features affects model predictions. The `plot_perturbation_analysis()` function helps to:
1. Generate feature attributions for a single observation
2. Evaluate them using perturbation
3. Visualize the results

In this example, we configure the perturbation analysis with several parameters:
- `perturbation_ratio = 0.5`: We perturb the first 50% of time points
- `auc_types=["MoRF", "LeRF"]`: We use two perturbation orders:
  - Most Relevant Features first (MoRF): Features perturbed in descending importance order
  - Least Relevant Features first (LeRF): Features perturbed in ascending importance order
- `perturbation_strategy = "zero"`: We replace feature values with zeros
- `features_per_step`: Controls how many features are perturbed in each step

For computational efficiency, we could increase `features_per_step`, though this reduces granularity of the results. With Wafer's time series length of 152, a perturbation ratio of 0.5 and `features_per_step = 1` means we'll perform 76 perturbations operations.

The example results below show effective feature attributions:
- The MoRF curve decreases relatively quickly (desirable), yielding a low area under the curve ($AUC_{MoRF} = 0.043$)
- The LeRF curve remains relatively unchanged until ~10% of features are perturbed (desirable), producing a higher AUC ($AUC_{LeRF} = 0.338$)

The degradation score (DS = 0.305) represents the difference between these curves, visualized as the grey area between them. Higher DS values generally indicate better attribution quality.

In [11]:
# Configuration for perturbation analysis
sample_idx: int = 1
method: str = "FO"
label: str | int = "predicted"
perturbation_strategy: str | int = "zero"
perturbation_ratio: float = 0.5
features_per_step: int = 1


# Run perturbation analysis for sample and show results
plot_perturbation_analysis(
    explainer=explainer,
    sample_idx=sample_idx,
    method=method,
    label=label,
    perturbation_strategy=perturbation_strategy,
    show_plot=True,
    auc_types=["MoRF", "LeRF"],
    plot_between=True,
    perturbation_ratio=perturbation_ratio,
    features_per_step=features_per_step,
)

╒════════════╤════════════╤════════════╕
│   AUC MoRF │   AUC LeRF │   DS Score │
╞════════════╪════════════╪════════════╡
│      0.043 │      0.338 │      0.305 │
╘════════════╧════════════╧════════════╛


<path d="M2.355212806987666 175.855854990097 L2.355212806987666 175.855854990097 L7.065638420962998 175.69247046789326 L11.77606403493833 175.69247046789326 L16.48648964891366 175.69247046789326 L21.196915262888993 175.69247046789326 L25.907340876864325 175.69247046789326 L30.617766490839657 175.855854990097 L35.32819210481499 175.69247046789326 L40.03861771879032 175.69247046789326 L44.74904333276565 175.855854990097 L49.459468946740984 175.855854990097 L54.169894560716315 175.855854990097 L58.88032017469165 175.855854990097 L63.59074578866698 175.855854990097 L68.30117140264231 175.855854990097 L73.01159701661764 175.855854990097 L77.72202263059297 175.855854990097 L82.4324482445683 175.855854990097 L87.14287385854364 175.855854990097 L91.85329947251897 175.855854990097 L96.5637250864943 39.26878358750532 L101.27415070046963 8.553030303030283 L105.98457631444496 18.029162575735 L110.6950019284203 39.26878358750532 L115.40542754239563 52.829461804075 L120.11585315637096 65.4098485467089 L124.82627877034629 72.92540458266487 L129.53670438432164 80.27757945197853 L134.24712999829694 84.68888437356672 L138.9575556122723 88.11989949899984 L143.6679812262476 91.38753233927017 L148.37840684022297 93.3481123510255 L153.08883245419827 95.30869222296577 L157.79925806817363 164.90927991388625 L162.50968368214893 175.69247046789326 L167.2201092961243 175.69247046789326 L171.9305349100996 175.69247046789326 L176.64096052407496 175.69247046789326 L181.35138613805026 175.855854990097 L186.06181175202562 175.855854990097 L190.77223736600092 175.69247046789326 L195.48266297997628 175.855854990097 L200.1930885939516 175.69247046789326 L204.90351420792695 175.855854990097 L209.61393982190225 175.855854990097 L214.3243654358776 175.855854990097 L219.0347910498529 175.69247046789326 L223.74521666382827 175.69247046789326 L228.45564227780358 175.855854990097 L233.16606789177894 175.855854990097 L237.87649350575424 65.89999316515633 L242.5869191197296 37.14482059151191 L247.2973447337049 30.446171507287985 L252.00777034768026 25.87148541905748 L256.71819596165557 24.237671515593377 L261.4286215756309 23.257377804616652 L266.13904718960623 22.767233186169236 L270.84947280358153 22.27708856772182 L275.5598984175569 21.62356390115255 L280.27032403153225 20.643274664257703 L284.98074964550756 20.479890142053975 L289.69117525948286 19.499605379241018 L294.4016008734582 19.989745523606558 L299.1120264874336 20.153130045810286 L303.8224521014089 20.153130045810286 L308.5328777153842 20.316510093932138 L313.24330332935955 20.970034760501406 L317.9537289433349 21.62356390115255 L322.6641545573102 21.62356390115255 L327.3745801712855 22.27708856772182 L332.0850057852609 22.767233186169236 L336.79543139923624 23.257377804616652 L341.50585701321154 23.584142374942232 L346.21628262718684 23.74752689714596 L350.9267082411622 24.07428699338965 L355.63713385513756 24.237671515593377 L360.34755946911287 24.401051563715228 L365.05798508308817 24.727816134040793 L369.76841069706353 25.21796075248821 L374.4788363110389 25.54472532281379 L379.1892619250142 25.54472532281379 L383.8996875389895 25.21796075248821 L388.61011315296486 25.38134080061006 L393.3205387669402 25.21796075248821 L398.0309643809155 25.54472532281379 L402.7413899948908 25.21796075248821 L407.4518156088662 25.54472532281379 L412.16224122284154 25.54472532281379 L416.87266683681685 25.21796075248821 L421.58309245079215 24.891196182162645 L426.2935180647675 25.38134080061006 L431.00394367874287 24.891196182162645 L435.7143692927182 25.21796075248821 L440.4247949066935 24.564431611837065 L445.13522052066884 24.727816134040793 L449.8456461346442 24.401051563715228 L454.5560717486195 24.401051563715228 L459.2664973625948 24.237671515593377 L463.97692297657017 23.42076232682038 L468.6873485905455 20.806654712379554 L473.39777420452083 16.885497764800192 L478.10819981849613 11.984051580325996 L482.8186254324715 12.147427154365957 L487.52905104644685 14.271390150359366 L492.23947666042216 16.068593050109087

### Alternative Perturbation Strategies

We can evaluate the same attribution using different perturbation strategies to assess robustness. For example, instead of zero replacement, we can use a constant value of 1. This choice is informative since we observed that relevant features in our example cluster around -1.

This alternative strategy yields a higher degradation score, suggesting improved discrimination between relevant and irrelevant features for this particular instance. However, we also notice that the MoRF perturbation curve increases after 40% perturbation, which may indicate some limitations in either the attribution method or perturbation strategy.

The implementation supports various perturbation approaches:
```python
available_perturbation_strategies = [
    "zero",             # Replace with 0
    "mean",             # Replace with instance mean
    "gaussian_noise",   # Replace with random gaussian noise
    "opposite",         # Replace with negated values
    "uniform_noise",    # Replace with uniform noise
    "subsequence_mean", # Replace with local mean
    "inverse",          # Replace with inverted values
    "ood_high",         # Replace with high out-of-distribution value
    "ood_low",          # Replace with low out-of-distribution value
]
```

Beyond these predefined strategies, you can also specify custom constant values as demonstrated below. Different perturbation strategies may perform better for different instances, highlighting the importance of considering multiple approaches when evaluating attributions.

In [12]:
perturbation_strategy: str | int = 1

plot_perturbation_analysis(
    explainer=explainer,
    sample_idx=sample_idx,
    method=method,
    label=label,
    perturbation_strategy=perturbation_strategy,
    show_plot=True,
    auc_types=["MoRF", "LeRF"],
    plot_between=True,
    perturbation_ratio=perturbation_ratio,
    features_per_step=features_per_step,
)

╒════════════╤════════════╤════════════╕
│   AUC MoRF │   AUC LeRF │   DS Score │
╞════════════╪════════════╪════════════╡
│      0.123 │      0.751 │      0.819 │
╘════════════╧════════════╧════════════╛


<path d="M2.355212806987666 175.855854990097 L2.355212806987666 175.855854990097 L7.065638420962998 175.69247046789326 L11.77606403493833 175.69247046789326 L16.48648964891366 175.69247046789326 L21.196915262888993 175.69247046789326 L25.907340876864325 175.69247046789326 L30.617766490839657 175.855854990097 L35.32819210481499 175.69247046789326 L40.03861771879032 175.69247046789326 L44.74904333276565 175.855854990097 L49.459468946740984 175.855854990097 L54.169894560716315 175.855854990097 L58.88032017469165 175.855854990097 L63.59074578866698 175.855854990097 L68.30117140264231 175.855854990097 L73.01159701661764 175.855854990097 L77.72202263059297 175.855854990097 L82.4324482445683 175.855854990097 L87.14287385854364 175.855854990097 L91.85329947251897 175.855854990097 L96.5637250864943 39.26878358750532 L101.27415070046963 8.553030303030283 L105.98457631444496 18.029162575735 L110.6950019284203 39.26878358750532 L115.40542754239563 52.829461804075 L120.11585315637096 65.4098485467089 L124.82627877034629 72.92540458266487 L129.53670438432164 80.27757945197853 L134.24712999829694 84.68888437356672 L138.9575556122723 88.11989949899984 L143.6679812262476 91.38753233927017 L148.37840684022297 93.3481123510255 L153.08883245419827 95.30869222296577 L157.79925806817363 164.90927991388625 L162.50968368214893 175.69247046789326 L167.2201092961243 175.69247046789326 L171.9305349100996 175.69247046789326 L176.64096052407496 175.69247046789326 L181.35138613805026 175.855854990097 L186.06181175202562 175.855854990097 L190.77223736600092 175.69247046789326 L195.48266297997628 175.855854990097 L200.1930885939516 175.69247046789326 L204.90351420792695 175.855854990097 L209.61393982190225 175.855854990097 L214.3243654358776 175.855854990097 L219.0347910498529 175.69247046789326 L223.74521666382827 175.69247046789326 L228.45564227780358 175.855854990097 L233.16606789177894 175.855854990097 L237.87649350575424 65.89999316515633 L242.5869191197296 37.14482059151191 L247.2973447337049 30.446171507287985 L252.00777034768026 25.87148541905748 L256.71819596165557 24.237671515593377 L261.4286215756309 23.257377804616652 L266.13904718960623 22.767233186169236 L270.84947280358153 22.27708856772182 L275.5598984175569 21.62356390115255 L280.27032403153225 20.643274664257703 L284.98074964550756 20.479890142053975 L289.69117525948286 19.499605379241018 L294.4016008734582 19.989745523606558 L299.1120264874336 20.153130045810286 L303.8224521014089 20.153130045810286 L308.5328777153842 20.316510093932138 L313.24330332935955 20.970034760501406 L317.9537289433349 21.62356390115255 L322.6641545573102 21.62356390115255 L327.3745801712855 22.27708856772182 L332.0850057852609 22.767233186169236 L336.79543139923624 23.257377804616652 L341.50585701321154 23.584142374942232 L346.21628262718684 23.74752689714596 L350.9267082411622 24.07428699338965 L355.63713385513756 24.237671515593377 L360.34755946911287 24.401051563715228 L365.05798508308817 24.727816134040793 L369.76841069706353 25.21796075248821 L374.4788363110389 25.54472532281379 L379.1892619250142 25.54472532281379 L383.8996875389895 25.21796075248821 L388.61011315296486 25.38134080061006 L393.3205387669402 25.21796075248821 L398.0309643809155 25.54472532281379 L402.7413899948908 25.21796075248821 L407.4518156088662 25.54472532281379 L412.16224122284154 25.54472532281379 L416.87266683681685 25.21796075248821 L421.58309245079215 24.891196182162645 L426.2935180647675 25.38134080061006 L431.00394367874287 24.891196182162645 L435.7143692927182 25.21796075248821 L440.4247949066935 24.564431611837065 L445.13522052066884 24.727816134040793 L449.8456461346442 24.401051563715228 L454.5560717486195 24.401051563715228 L459.2664973625948 24.237671515593377 L463.97692297657017 23.42076232682038 L468.6873485905455 20.806654712379554 L473.39777420452083 16.885497764800192 L478.10819981849613 11.984051580325996 L482.8186254324715 12.147427154365957 L487.52905104644685 14.271390150359366 L492.23947666042216 16.068593050109087

# Paper Experiment Results

## Classifier Performance

This section provides access to the experimental results presented in our paper. We begin by examining the classifier performance metrics across all datasets and architectures.

The table displays training, validation, and test accuracy and F1 scores for each model configuration. These results correspond to Table 1 in our paper, showing the classification performance that forms the foundation for our attribution analysis.

The trained model weights are stored in the `results/models` directory and can be loaded using the procedure demonstrated in the "Load trained model" section above.

In [13]:
# check performance metrics of classifiers for all datasets and models
performance_fname = "results/models/performance.csv"
performance_df = pd.read_csv(performance_fname)
performance_df.round(4)

dataset          model  train_accuracy  val_accuracy  \
0            Wafer         ResNet          1.0000        1.0000   
1            Wafer  InceptionTime          1.0000        1.0000   
2            FordA         ResNet          0.9990        0.9307   
3            FordA  InceptionTime          1.0000        0.9445   
4            FordB         ResNet          1.0000        0.9299   
5            FordB  InceptionTime          0.9966        0.9382   
6  ElectricDevices         ResNet          0.9807        0.9127   
7  ElectricDevices  InceptionTime          0.9874        0.8953   

   test_accuracy  train_f1  val_f1  test_f1  
0         0.9925    1.0000  1.0000   0.9924  
1         0.9982    1.0000  1.0000   0.9982  
2         0.9371    0.9990  0.9306   0.9371  
3         0.9523    1.0000  0.9445   0.9523  
4         0.8037    1.0000  0.9299   0.8037  
5         0.8494    0.9966  0.9381   0.8493  
6         0.7157    0.9808  0.9127   0.7005  
7         0.7024    0.9875  0.8956   0.6894

## Perturbation Results

This section shows how to access the perturbation analysis results from our experiments. The data is stored in CSV format at `results/perturbation_results/paper_results/compiled_results.csv` for each experimental configuration.

The `load_and_format_experiment_results()` utility function simplifies data loading and preprocessing. This function offers filtering options through the `perturbation_mode` parameter:
- `perturbation_mode = "named"`: Loads results for named strategies (Gauss, Inv, Opp, SubMean, Unif, Zero)
- `perturbation_mode = "constant"`: Loads results for constant-value perturbations

Note that "zero" in named strategies and 0 in constant strategies represent identical perturbation approaches. We include zero in the named strategies for consistency with prior literature.

The results contain detailed metrics for each experimental condition:
- Instance identifiers and class labels (true and predicted)
- Evaluation metrics (AUC for MoRF and LeRF perturbation orders)
- Calculated degradation scores (DS)
- Experimental metadata (dataset, classifier, attribution method)

This dataset enables reproduction of all analyses presented in our paper and supports additional investigations into class-dependent perturbation effects.

In [14]:
# where the results from perturbation experiments are saved
results_fname = "compiled_results.csv"

RESULTS_DIR = Path.cwd() / "results/perturbation_results/paper_results"
RESULTS_PATH = RESULTS_DIR / results_fname
assert RESULTS_PATH.exists(), f"Results file not found at: {RESULTS_PATH}"

In [15]:
# load results for "named" perturbation strategies separately
results_df_named = load_and_format_experiment_results(
    RESULTS_PATH, perturbation_mode="named"
)

print(f"Classifiers: {results_df_named['model_name'].unique()}")
print(f"Attribution Methods: {results_df_named['attribution_method'].unique()}")
print(f"Datasets: {results_df_named['dataset_name'].unique()}")
print(f"Perturbation strategies: {results_df_named['perturbation_strategy'].unique()}")
print(f"Results dimensions: {results_df_named.shape}")
results_df_named.drop(columns="probabilities")

Classifiers: ['ResNet' 'InceptionTime']
Attribution Methods: ['GS' 'FO' 'IG' 'SG' 'GR']
Datasets: ['Wafer' 'FordB' 'FordA' 'ElectricDevices']
Perturbation strategies: ['Inv' 'SubMean' 'Unif' 'Gauss' 'Opp' 'Zero']
Results dimensions: (234000, 12)


idx  true_label  predicted_label  auc_morf  auc_lerf        ds  \
2100    2625           0                0  0.979224  0.936108 -0.000774   
2101    2674           0                0  0.915738  0.858674  0.000150   
2102    4246           0                0  0.941799  0.882541 -0.000009   
2103    2167           0                0  0.939960  0.903231 -0.003626   
2104    3912           0                0  0.931968  0.932883  0.010144   
...      ...         ...              ...       ...       ...       ...   
545995  1675           6                4  0.169130  0.267614  0.082983   
545996  1700           6                3  0.301534  0.109045 -0.137937   
545997  1434           6                6  0.307993  0.434978  0.140919   
545998  1693           6                4  0.400427  0.374040  0.052629   
545999  1718           6                3  0.417721  0.072995 -0.178679   

           dataset_name model_name attribution_method perturbation_strategy  \
2100              Wafer     ResNet                 GS                   Inv   
2101              Wafer     ResNet                 GS                   Inv   
2102              Wafer     ResNet                 GS                   Inv   
2103              Wafer     ResNet                 GS                   Inv   
2104              Wafer     ResNet                 GS                   Inv   
...                 ...        ...                ...                   ...   
545995  ElectricDevices     ResNet                 IG                   Opp   
545996  ElectricDevices     ResNet                 IG                   Opp   
545997  ElectricDevices     ResNet                 IG                   Opp   
545998  ElectricDevices     ResNet                 IG                   Opp   
545999  ElectricDevices     ResNet                 IG                   Opp   

        n_attributions  
2100               300  
2101               300  
2102               300  
2103               300  
2104               300  
...                ...  
545995             300  
545996             300  
545997             300  
545998             300  
545999             300  

[234000 rows x 11 columns]

In [16]:
# load results for constant perturbation strategies separately
results_df_constant = load_and_format_experiment_results(
    RESULTS_PATH, perturbation_mode="constant"
)

print(f"Classifiers: {results_df_constant['model_name'].unique()}")
print(f"Attribution Methods: {results_df_constant['attribution_method'].unique()}")
print(f"Datasets: {results_df_constant['dataset_name'].unique()}")
print(
    f"Perturbation strategies: {results_df_constant['perturbation_strategy'].unique()}"
)
print(f"Results dimensions: {results_df_constant.shape}")
results_df_constant.drop(columns="probabilities")

Classifiers: ['InceptionTime' 'ResNet']
Attribution Methods: ['FO' 'SG' 'IG' 'GS' 'GR']
Datasets: ['ElectricDevices' 'FordB' 'FordA' 'Wafer']
Perturbation strategies: ['1.5' '-1' '1' '2' '-0.5' '0' '0.5' '-2' '-1.5']
Results dimensions: (351000, 12)


idx  true_label  predicted_label  auc_morf  auc_lerf        ds  \
0       7381           0                5  0.179608  0.066264 -0.131603   
1        496           0                4  0.527483  0.801977  0.284112   
2       7355           0                0  0.021424  0.155690  0.084731   
3       3240           0                0  0.022714  0.150046  0.117669   
4       7356           0                3  0.376539  0.668450  0.308652   
...      ...         ...              ...       ...       ...       ...   
543895   573           1                1  0.076219  0.156905  0.077213   
543896   178           1                1  0.053277  0.080145  0.023871   
543897   809           1                1  0.051478  0.090335  0.035659   
543898   172           1                1  0.088861  0.085707 -0.002937   
543899   403           1                0  0.936680  0.946887  0.000625   

           dataset_name     model_name attribution_method  \
0       ElectricDevices  InceptionTime                 FO   
1       ElectricDevices  InceptionTime                 FO   
2       ElectricDevices  InceptionTime                 FO   
3       ElectricDevices  InceptionTime                 FO   
4       ElectricDevices  InceptionTime                 FO   
...                 ...            ...                ...   
543895            FordB         ResNet                 SG   
543896            FordB         ResNet                 SG   
543897            FordB         ResNet                 SG   
543898            FordB         ResNet                 SG   
543899            FordB         ResNet                 SG   

       perturbation_strategy  n_attributions  
0                        1.5             300  
1                        1.5             300  
2                        1.5             300  
3                        1.5             300  
4                        1.5             300  
...                      ...             ...  
543895                  -0.5             300  
543896                  -0.5             300  
543897                  -0.5             300  
543898                  -0.5             300  
543899                  -0.5             300  

[351000 rows x 11 columns]

### Class-adjusted Correctness Metrics

The `calculate_class_adjusted_metric()` function aggregates the degradation score (DS) metric over all experimental conditions. The parameter α controls the strength of class-specific penalization:
- `α = 0`: Equivalent to taking the mean across experimental conditions
- `α > 0`: Penalizes the average metric with the difference of average metrics between class pairs

The example below calculates results with `α = 1` for the named perturbation strategies.

In [17]:
alpha: float = 1  # weight for penalty term in class-adjusted metric

experimental_conditions = [
    "dataset_name",
    "model_name",
    "attribution_method",
    "perturbation_strategy",
]

aggregate_ds_results = calculate_class_adjusted_metric(
    df=results_df_named,
    metric_col="ds",
    group_cols=experimental_conditions,
    class_col="true_label",
    alpha=alpha,
)
aggregate_ds_results


dataset_name     model_name attribution_method perturbation_strategy  \
0    ElectricDevices  InceptionTime                 FO                 Gauss   
1    ElectricDevices  InceptionTime                 FO                   Inv   
2    ElectricDevices  InceptionTime                 FO                   Opp   
3    ElectricDevices  InceptionTime                 FO               SubMean   
4    ElectricDevices  InceptionTime                 FO                  Unif   
..               ...            ...                ...                   ...   
235            Wafer         ResNet                 SG                   Inv   
236            Wafer         ResNet                 SG                   Opp   
237            Wafer         ResNet                 SG               SubMean   
238            Wafer         ResNet                 SG                  Unif   
239            Wafer         ResNet                 SG                  Zero   

     adjusted_metric  
0          -0.091163  
1          -0.035715  
2           0.122114  
3           0.229013  
4           0.022093  
..               ...  
235        -0.000187  
236        -0.000804  
237        -0.005194  
238         0.001403  
239        -0.001242  

[240 rows x 5 columns]

### Aggregate Experimental Results

Pre-computed aggregated results from `scripts/aggregate_experiment_results.py` are available in four tables:
1. `average_ds_table.csv`: Mean DS for named strategies
2. `adjusted_ds_table.csv`: Class-adjusted DS for named strategies (α=1)
3. `constant_average_ds_table.csv`: Mean DS for constant-value strategies
4. `constant_adjusted_ds_table.csv`: Class-adjusted DS for constant-value strategies (α=1)

The example below loads `adjusted_ds_table.csv`, reproducing the results presented in our paper.

In [18]:
agg_results_paths = sorted([f for f in (RESULTS_DIR / "tables").iterdir()])
print("Aggregated results tables:\n", [f.name for f in agg_results_paths])


Aggregated results tables:
 ['adjusted_ds_table.csv', 'average_ds_table.csv', 'constant_adjusted_ds_table.csv', 'constant_average_ds_table.csv']


In [19]:
fname: str = "adjusted_ds_table.csv"
file_path = [f for f in agg_results_paths if fname in f.name][0]


agg_results_df = pd.read_csv(file_path, index_col=[0, 1], header=[0, 1]).round(3)
agg_results_df

Model                        ResNet                             InceptionTime  \
Attribution                      GR     IG     SG     GS     FO            GR   
Dataset         Perturbation                                                    
FordA           Gauss        -0.011  0.003  0.001 -0.078  0.003        -0.008   
                Inv          -0.005  0.000  0.000  0.000  0.001        -0.007   
                Opp          -0.053  0.001  0.000  0.001  0.001        -0.104   
                SubMean      -0.082  0.003  0.000  0.002  0.005        -0.188   
                Unif         -0.025  0.000  0.000  0.000  0.000        -0.028   
                Zero         -0.082  0.003  0.001  0.002  0.005        -0.197   
FordB           Gauss        -0.004  0.003 -0.003 -0.049  0.006        -0.068   
                Inv          -0.001  0.000 -0.001  0.000  0.000        -0.013   
                Opp          -0.023  0.003  0.001  0.002  0.004        -0.091   
                SubMean      -0.044  0.006  0.000  0.005  0.010        -0.158   
                Unif         -0.007  0.001  0.000  0.001  0.001        -0.017   
                Zero         -0.044  0.006  0.000  0.005  0.010        -0.159   
Wafer           Gauss        -0.149 -0.214  0.001  0.003 -0.367         0.003   
                Inv           0.008  0.003 -0.000  0.002  0.002        -0.026   
                Opp          -0.042  0.002 -0.001  0.003  0.003        -0.021   
                SubMean       0.034  0.018 -0.005  0.037  0.038         0.014   
                Unif         -0.020  0.001  0.001  0.002  0.001         0.002   
                Zero         -0.047  0.007 -0.001  0.011  0.013         0.012   
ElectricDevices Gauss        -0.039 -0.036 -0.020 -0.029 -0.044         0.011   
                Inv          -0.024  0.012  0.047  0.009  0.025        -0.082   
                Opp          -0.029  0.104  0.001  0.096  0.156         0.039   
                SubMean       0.078  0.130  0.141  0.136  0.219         0.075   
                Unif          0.026  0.031 -0.003  0.020  0.082        -0.004   
                Zero         -0.010  0.089  0.031  0.063  0.226         0.053   

Model                                                     
Attribution                      IG     SG     GS     FO  
Dataset         Perturbation                              
FordA           Gauss         0.001 -0.000 -0.049  0.002  
                Inv           0.000 -0.000  0.000  0.000  
                Opp           0.000 -0.000  0.000  0.000  
                SubMean       0.000  0.001  0.000 -0.000  
                Unif         -0.000 -0.000  0.000 -0.000  
                Zero          0.000  0.001 -0.000 -0.001  
FordB           Gauss         0.015  0.009 -0.046  0.026  
                Inv           0.003  0.001  0.002  0.003  
                Opp           0.004 -0.041  0.004  0.005  
                SubMean       0.013 -0.134  0.014  0.014  
                Unif          0.001  0.001  0.001  0.001  
                Zero          0.013 -0.134  0.015  0.015  
Wafer           Gauss        -0.201 -0.004  0.033 -0.419  
                Inv           0.001 -0.012  0.008  0.009  
                Opp           0.002 -0.011  0.010  0.008  
                SubMean       0.048 -0.000  0.018  0.028  
                Unif          0.002 -0.014  0.008  0.008  
                Zero          0.009 -0.023  0.036  0.016  
ElectricDevices Gauss        -0.015  0.045  0.027 -0.091  
                Inv           0.018 -0.045  0.027 -0.036  
                Opp           0.140  0.041  0.116  0.122  
                SubMean       0.151  0.081  0.134  0.229  
                Unif          0.055  0.026  0.041  0.022  
                Zero          0.118  0.038  0.104  0.162

### Plots

#### Perturbation Metric Distributions

The code below reproduces Figures 3a and 3b from the paper. You can modify the parameters at the top of the code block to visualize results for different experimental conditions.

In [20]:
dataset: str = "FordB"
model: str = "InceptionTime"
perturbation_strategy: str = "SubMean"
attribution_methods = ["GR", "IG", "SG", "GS", "FO"]

# filter data for plotting
plot_data = results_df_named.copy().query(
    "perturbation_strategy == @perturbation_strategy"
    "& attribution_method in @attribution_methods"
    "& dataset_name == @dataset"
    "& model_name == @model"
)

# plot distribution of metric across attribution methods for a dataset,
# model and perturbation strategy
plot_kwargs = {
    "data": plot_data,
    "x_col": "attribution_method",
    "y_col": "ds",
    "x_levels": attribution_methods,
    "x_label": "Attribution Method",
    "y_label": "Degradation Score (DS)",
    "plot_size": (width, height),
}
ds_dist_plot = plot_metric_distributions(**plot_kwargs)
ds_dist_plot_stratified = plot_metric_distributions(
    **plot_kwargs, color_by="true_label"
)

# show plots
ds_dist_plot += theme_paper()
ds_dist_plot_stratified += theme_paper()
ds_dist_plot.show()
ds_dist_plot_stratified.show()

# from lets_plot import ggsave
# ggsave(ds_dist_plot, "ds_dist_avg_inceptiontime.pdf")
# ggsave(ds_dist_plot_stratified, "ds_dist_by_class_inceptiontime.pdf")


<path d="M305.78541960152484 309.39726862541846 L305.78541960152484 309.39726862541846 L305.78253504489476 309.0846662767302 L305.77992216666036 308.7720639280419 L305.77755234209826 308.4594615793536 L305.7753913934885 308.14685923066537 L305.77340016383937 307.8342568819771 L305.7715351995312 307.5216545332888 L305.7697495247001 307.2090521846005 L305.7679934873387 306.8964498359123 L305.7662156548449 306.58384748722403 L305.76436373520244 306.27124513853573 L305.7623854991733 305.9586427898475 L305.7602296788814 305.6460404411592 L305.75784681894936 305.33343809247094 L305.7551900579268 305.0208357437827 L305.7522158200384 304.7082333950944 L305.7488844002337 304.39563104640615 L305.74516042902826 304.08302869771785 L305.74101320756125 303.7704263490296 L305.73641690754414 303.4578240003413 L305.73135063517014 303.14522165165306 L305.7257983624636 302.83261930296476 L305.7197487338103 302.5200169542765 L305.7131947593859 302.2074146055882 L305.7061334107537 301.89481225689997 L305.6985651369183 301.58220990821167 L305.6904933214979 301.2696075595234 L305.6819237033367 300.9570052108351 L305.67286378377577 300.6444028621469 L305.66332224389566 300.33180051345863 L305.65330839435364 300.01919816477033 L305.6428316789768 299.7065958160821 L305.6319012510992 299.3939934673938 L305.6205256388124 299.08139111870554 L305.6087125119386 298.7687887700173 L305.5964685597345 298.456186421329 L305.58379948422237 298.1435840726407 L305.5707101097513 297.83098172395245 L305.5572046050572 297.5183793752642 L305.5432868098476 297.2057770265759 L305.52896065392576 296.8931746778876 L305.5142306532163 296.58057232919936 L305.4991024638725 296.2679699805111 L305.483583473042 295.9553676318228 L305.46768340292994 295.64276528313457 L305.4514149035839 295.3301629344463 L305.4347941093967 295.017560585758 L305.4178411346843 294.7049582370698 L305.4005804848653 294.3923558883815 L305.3830413617129 294.07975353969323 L305.36525784382366 293.7671511910049 L305.3472689267916 293.4545488423167 L305.3291184114854 293.1419464936284 L305.3108546332114 292.82934414494014 L305.29253002926913 292.51674179625184 L305.27420054733597 292.2041394475636 L305.25592490211307 291.8915370988753 L305.23776369256507 291.57893475018705 L305.2197783967487 291.26633240149874 L305.2020302654964 290.9537300528105 L305.18457913996406 290.64112770412225 L305.16748222113995 290.32852535543395 L305.1507928217337 290.0159230067457 L305.1345591323386 289.7033206580574 L305.1188230343174 289.39071830936916 L305.10361899147205 289.07811596068086 L305.08897305121366 288.7655136119926 L305.07490198367617 288.4529112633044 L305.0614125840682 288.14030891461607 L305.04850115962154 287.82770656592777 L305.0361532178749 287.5151042172395 L305.0243433678669 287.2025018685513 L305.0130354402543 286.889899519863 L305.0021828265849 286.57729717117473 L304.9917290321147 286.26469482248643 L304.9816084308494 285.9520924737982 L304.97174720607586 285.6394901251099 L304.9620644547033 285.32688777642164 L304.95247342940775 285.0142854277334 L304.9428828889884 284.7016830790451 L304.93319852462105 284.38908073035685 L304.923324427902 284.07647838166855 L304.91316456577 283.7638760329803 L304.90262422759173 283.451273684292 L304.8916114108894 283.13867133560376 L304.8800381143302 282.82606898691546 L304.86782150961994 282.5134666382272 L304.85488496775247 282.2008642895389 L304.84115891954013 281.88826194085067 L304.8265815353561 281.5756595921624 L304.81109921440554 281.2630572434741 L304.79466687945217 280.9504548947859 L304.7772480785918 280.6378525460976 L304.7588149012277 280.32525019740933 L304.7393477207005 280.01264784872103 L304.7188347809081 279.7000455000328 L304.69727164858085 279.38744315134454 L304.67466055652994 279.07484080265624 L304.65100966605496 278.76223845396794 L304.6263322786965 278.4496361052797 L304.6006460285839 278.13703375659145 L304.57397208672205 277.82443140790315 L304.54633440765963 277.51182905921485 L304.5177590471044 277.1992267105266 L304.4882735762237 276.886

<path d="M277.75315692360687 265.9660166473616 L277.75315692360687 265.9660166473616 L277.775128366459 265.76770653395937 L277.8308405212776 265.56939642055715 L277.8971744777884 265.37108630715494 L277.95324855602837 265.1727761937527 L277.99004084770934 264.9744660803505 L278.00943619086036 264.7761559669483 L278.01779153547113 264.57784585354614 L278.0207614050242 264.37953574014387 L278.02163761832355 264.1812256267417 L278.0218530441863 263.9829155133395 L278.0218973022495 263.7846053999373 L278.02190491516257 263.58629528653506 L278.02190601317756 263.38798517313285 L278.0219061461145 263.18967505973063 L278.0219061596363 262.9913649463284 L278.0219061607926 262.7930548329262 L278.0219061608758 262.594744719524 L278.0219061608808 262.3964346061218 L278.02190616088103 262.19812449271956 L278.02190616088103 261.99981437931734 L278.02190616088103 261.8015042659151 L278.02190616088103 261.6031941525129 L278.02190616088103 261.4048840391107 L278.02190616088103 261.20657392570854 L278.02190616088103 261.0082638123063 L278.02190616088103 260.8099536989041 L278.02190616088103 260.6116435855019 L278.02190616088103 260.4133334720997 L278.02190616088103 260.21502335869747 L278.02190616088103 260.01671324529525 L278.02190616088103 259.81840313189304 L278.02190616088103 259.6200930184908 L278.02190616088103 259.4217829050886 L278.02190616088103 259.2234727916864 L278.02190616088103 259.02516267828423 L278.02190616088103 258.82685256488196 L278.02190616088103 258.6285424514798 L278.02190616088103 258.4302323380776 L278.02190616088103 258.2319222246754 L278.02190616088103 258.03361211127316 L278.02190616088103 257.83530199787094 L278.02190616088103 257.6369918844687 L278.02190616088103 257.4386817710665 L278.02190616088103 257.2403716576643 L278.02190616088103 257.0420615442621 L278.02190616088103 256.84375143085987 L278.02190616088103 256.64544131745765 L278.02190616088103 256.44713120405544 L278.02190616088103 256.2488210906532 L278.02190616088103 256.05051097725107 L278.02190616088103 255.85220086384885 L278.02190616088103 255.6538907504466 L278.02190616088103 255.45558063704442 L278.02190616088103 255.2572705236422 L278.02190616088103 255.05896041024 L278.02190616088103 254.86065029683778 L278.02190616088103 254.66234018343556 L278.02190616088103 254.46403007003335 L278.02190616088103 254.26571995663113 L278.02190616088103 254.06740984322892 L278.02190616088103 253.8690997298267 L278.02190616088103 253.6707896164245 L278.02190616088103 253.4724795030223 L278.02190616088103 253.27416938962008 L278.02190616088103 253.0758592762179 L278.02190616088103 252.87754916281565 L278.02190616088103 252.67923904941347 L278.02190616088103 252.48092893601125 L278.02190616088103 252.28261882260904 L278.02190616088103 252.08430870920682 L278.02190616088103 251.8859985958046 L278.02190616088103 251.6876884824024 L278.02190616088103 251.48937836900018 L278.02190616088103 251.29106825559796 L278.02190616088103 251.09275814219575 L278.02190616088103 250.89444802879356 L278.02190616088103 250.69613791539135 L278.02190616088103 250.49782780198913 L278.02190616088103 250.29951768858692 L278.02190616088103 250.10120757518473 L278.02190616088103 249.90289746178252 L278.02190616088103 249.7045873483803 L278.02190616088103 249.50627723497809 L278.02190616088103 249.30796712157587 L278.02190616088103 249.10965700817366 L278.02190616088103 248.91134689477144 L278.02190616088103 248.71303678136923 L278.02190616088103 248.514726667967 L278.02190616088103 248.3164165545648 L278.02190616088103 248.1181064411626 L278.02190616088103 247.9197963277604 L278.02190616088103 247.72148621435818 L278.02190616088103 247.52317610095596 L278.02190616088103 247.32486598755378 L278.02190616088103 247.12655587415156 L278.02190616088103 246.92824576074935 L278.02190616088103 246.72993564734713 L278.02190616088103 246.53162553394492 L278.02190616088103 246.3333154205427 L278.02190616088103 246.1350053071405 L278.02190616088103 245.93669519373827 L278.02190616088103 245.738385080336

#### Parallel Coordinates Plot

The following code reproduces Figures 4a and 4b. You can adjust the parameters to visualize different experimental configurations.

In [21]:
dataset: str = "FordB"
model: str = "InceptionTime"
attribution_method: str = "FO"
color_by: str = "true_label"


def filter_and_format_plot_data(df) -> pd.DataFrame:
    """Convenience function to filter and format data for plotting"""
    filter_str = (
        "attribution_method == @attribution_method"
        "& dataset_name == @dataset"
        "& model_name == @model"
    )
    plot_data = df.copy().query(filter_str)
    plot_data.loc[:, label] = plot_data[color_by].astype(str)
    plot_data = plot_data.sort_values(color_by)
    return plot_data


plot_data_named = filter_and_format_plot_data(results_df_named)
plot_data_constant = filter_and_format_plot_data(results_df_constant)

# plot parallel coordinates for perturbation strategies
plot_kwargs_parallel = {
    "x_col": "perturbation_strategy",
    "x_label": "Perturbation Strategy",
    "y_col": "ds",
    "y_label": "Degradation Score (DS)",
    "group_col": color_by,
    "instance_id_col": "idx",
    "plot_size": (width, height),
}
pc_plot_named = plot_parallel_coords(
    data=plot_data_named, order="ascending", **plot_kwargs_parallel
)
pc_plot_constant = plot_parallel_coords(
    data=plot_data_constant, order="name", **plot_kwargs_parallel
)
pc_plot_named += theme_paper()
pc_plot_constant += theme_paper()

pc_plot_named.show()
pc_plot_constant.show()

# from lets_plot import ggsave
# ggsave(pc_plot_named, "pcoords_adaptive_perturbations.pdf")
# ggsave(pc_plot_constant, "pcoords_constant_perturbations.pdf")


<path d="M22

<path d="M14.570057062600979 284.81368728174937 L14.570057062600979 284.81368728174937 L87.42034237560587 287.4071634245296

#### Example of Desirable MoRF and LeRF Perturbation Curves

This following code reproduces Figure 2, showing the ideal pattern where:
- MoRF curve (perturbing important features) drops rapidly
- LeRF curve (perturbing unimportant features) remains stable initially
- The gap between curves (DS) is substantial


In [22]:
def create_curve(
    n_points: int,
    curve_type: str = "quick_drop",
    params: dict = None,
    noise_level: float = 0,
    smoothing: str = "savgol",
    smoothing_params: dict = None,
) -> np.ndarray:
    """Create a perturbation curve with specified characteristics.

    Args:
        n_points: Number of points to generate
        curve_type: Either "quick_drop" or "delayed_drop"
        params: Parameters specific to the curve type
        noise_level: Amount of noise to add
        smoothing: Type of smoothing to apply ("none", "savgol", "gaussian")
        smoothing_params: Parameters for the smoothing function
    Returns:
        np.ndarray: Perturbation curve values
    """
    from scipy.ndimage import gaussian_filter1d
    from scipy.signal import savgol_filter

    # Default parameters
    params = params or {}
    smoothing_params = smoothing_params or {}
    curve = np.full(n_points, 0.05)

    if curve_type == "quick_drop":
        # Quick drop curve (MoRF)
        drop_idx = int(params.get("drop_end", 0.25) * n_points)
        if drop_idx > 0:
            x_drop = np.linspace(0, np.pi, drop_idx)
            curve[:drop_idx] = 0.95 - 0.9 * (1 - np.cos(x_drop)) / 2
    elif curve_type == "delayed_drop":
        # Delayed drop curve (LeRF)
        start_idx = int(params.get("start_drop", 0.5) * n_points)
        end_idx = int(params.get("end_drop", 0.8) * n_points)
        curve[:start_idx] = 0.95
        # Create sigmoid drop between start and end
        if start_idx < end_idx:
            x_drop = np.linspace(0, 1, end_idx - start_idx)
            steepness = params.get("steepness", 10)
            curve[start_idx:end_idx] = 0.95 - 0.9 / (
                1 + np.exp(-steepness * (x_drop - 0.5))
            )

    # Apply smoothing if requested
    if smoothing == "savgol":
        # Savitzky-Golay filter (preserves shape characteristics)
        window_length = smoothing_params.get("window_length", 15)
        poly_order = smoothing_params.get("poly_order", 3)
        # Ensure window length is odd
        window_length = window_length + 1 if window_length % 2 == 0 else window_length
        # Ensure window length is not greater than n_points
        window_length = min(
            window_length, n_points - 2 if n_points % 2 == 0 else n_points - 1
        )
        if window_length > poly_order + 1:  # Valid window length check
            curve = savgol_filter(curve, window_length, poly_order)

    elif smoothing == "gaussian":
        # Gaussian filter (simple and effective smoothing)
        sigma = smoothing_params.get("sigma", 2.0)
        curve = gaussian_filter1d(curve, sigma)

    # Add noise if specified
    if noise_level > 0:
        curve += noise_level * np.random.randn(n_points)

    # Ensure exact endpoints and valid range
    curve[0] = 0.95
    curve[-1] = 0.05
    return np.clip(curve, 0.05, 0.95)


# Generate example curves
np.random.seed(42)
n_points = 100
morf_curve = create_curve(n_points, "quick_drop", {"drop_end": 0.3}, noise_level=0)
lerf_curve = create_curve(
    n_points, "delayed_drop", {"start_drop": 0.4, "end_drop": 0.85}, noise_level=0
)

# Create result object and plot
high_ds_example = PerturbationResult(
    scores={"MoRF": morf_curve.tolist(), "LeRF": lerf_curve.tolist()},
    auc_scores={"MoRF": 0.3, "LeRF": 0.7},
)

# Plot perturbation curves
ds_method_example_plot = plot_perturbation_analysis_curves(
    results=high_ds_example,
    title="",
    plot_between=True,
    perturbation_ratio=1,
    plot_size=(width, height),
)

ds_method_example_plot += theme(
    legend_position=[0.985, 1],
    legend_justification=[1, 1],
    legend_direction="vertical",
    legend_background=element_rect(color="grey", size=0.1),
) + labs(color="Perturbation Order", fill="Perturbation Type", title="")

ds_method_example_plot += theme_paper()
ds_method_example_plot.show()

# from lets_plot import ggsave
# ggsave(ds_method_example_plot, "ds_method_example.pdf")


<path d="M28.26203092121547 29.946141732283422 L28.26203092121547 29.946141732283422 L33.971532117420615 29.94614173228348 L39.68103331362576 29.946141732283422 L45.3905345098309 29.946141732283422 L51.10003570603605 29.946141732283422 L56.8095369022412 29.946141732283422 L62.51903809844634 29.946141732283422 L68.22853929465148 29.946141732283422 L73.93804049085664 29.946141732283422 L79.64754168706179 29.946141732283422 L85.35704288326693 29.946141732283422 L91.06654407947207 29.946141732283422 L96.7760452756772 29.946141732283422 L102.48554647188236 29.946141732283422 L108.19504766808751 29.946141732283422 L113.90454886429265 29.946141732283422 L119.6140500604978 29.946141732283422 L125.32355125670294 29.946141732283422 L131.0330524529081 29.946141732283422 L136.74255364911323 29.946141732283422 L142.4520548453184 29.946141732283422 L148.1615560415235 29.946141732283422 L153.87105723772868 29.946141732283422 L159.58055843393385 29.946141732283422 L165.29005963013896 29.946141732283422 L170.99956082634412 29.946141732283422 L176.70906202254923 29.946141732283422 L182.4185632187544 29.946141732283422 L188.12806441495957 29.946141732283422 L193.83756561116468 29.946141732283422 L199.54706680736984 29.946141732283422 L205.25656800357496 29.946141732283422 L210.96606919978012 29.946141732283422 L216.6755703959853 29.946141732283422 L222.3850715921904 29.946141732283422 L228.09457278839557 29.946141732283422 L233.80407398460073 29.946141732283422 L239.51357518080584 30.079735475216182 L245.223076377011 30.360827183563742 L250.93257757321618 30.73857409165788 L256.6420787694213 31.220683455006622 L262.35157996562646 31.81674308201201 L268.06108116183157 32.53864152630496 L273.77058235803673 33.401052970328806 L279.4800835542419 34.42197301304725 L285.189584750447 35.623267581840025 L290.8990859466522 37.03115520929674 L296.6085871428573 38.67647407485458 L302.3180883390624 40.85097331808021 L308.02758953526757 43.54415705961446 L313.73709073147273 46.86450706799667 L319.44659192767784 50.933785071349746 L325.156093123883 55.88328462118602 L330.8655943200882 61.84697140828871 L336.5750955162933 68.95107783156988 L342.28459671249846 77.30035471116881 L347.9940979087036 86.96209258680355 L353.70359910490873 97.94998932873469 L359.4131003011139 110.21062874652756 L365.122601497319 123.61543867857338 L370.8321026935242 137.9603867409895 L376.54160388972934 152.97446589479853 L382.25110508593446 168.3365271446324 L387.9606062821396 183.69858839446627 L393.6701074783448 198.71266754827528 L399.3796086745499 213.0576156106914 L405.08910987075507 226.46242554273726 L410.79861106696023 238.72306496053014 L416.50811226316534 249.7109617024612 L422.2176134593705 259.372699578096 L427.9271146555756 267.72197645769484 L433.6366158517808 274.8260828809761 L439.34611704798596 280.78976966807875 L445.05561824419107 285.739269217915 L450.76511944039623 289.8085472212681 L456.4746206366014 293.1288972296503 L462.1841218328065 295.8220809711846 L467.8936230290117 297.99658021441024 L473.60312422521685 299.6418990799681 L479.31262542142196 301.04978670742474 L485.0221266176271 302.2510812762175 L490.7316278138323 303.272001318936 L496.4411290100374 304.13441276295987 L502.15063020624257 304.8563112072528 L507.8601314024477 305.4523708342582 L513.5696325986529 305.9344801976069 L519.279133794858 306.3122271057011 L524.9886349910631 306.59331881404864 L530.6981361872683 306.72691255698305 L536.4076373834735 306.72691255698305 L542.1171385796786 306.72691255698305 L547.8266397758837 306.72691255698305 L553.5361409720889 306.72691255698294 L559.245642168294 306.72691255698305 L564.9551433644991 306.72691255698305 L570.6646445607043 306.72691255698305 L576.3741457569093 306.72691255698305 L582.0836469531146 306.72691255698305 L587.7931481493197 306.72691255698305 L593.5026493455248 306.72691255698305 L593.5026493455248 306.72691255698305 L587.7931481493197 306.72691255698305 L582.0836469531146 306.72691255698305 L576.3741457569093 306.72691255698305 L570.66

## Appendix: plots of datasets

In [23]:
n_samples_to_vis: int = 3
datasets = ["FordA", "FordB", "Wafer", "ElectricDevices"]

for dataset in datasets:
    data = load_ucr_data(dataset, remap_labels_ascending=True, on_disk=False)
    ts_samples_plot = vis_time_series_classification_samples(
        data.to_plotting_df(split="train"),
        n_samples_per_label=n_samples_to_vis,
        alpha=1,
        n_col=2,
        title="",
        random_state=42,
    )
    if data.n_classes == 2:
        ts_samples_plot += ggsize(*get_plot_dimensions(scale=2, aspect_ratio=0.35))
    else:
        plot_dimensions = get_plot_dimensions(scale=2, aspect_ratio=0.35)
        plot_dimensions = plot_dimensions[0], plot_dimensions[1] * data.n_classes / 2
        ts_samples_plot += ggsize(*plot_dimensions)
    ts_samples_plot += theme_paper(legend_position=None)

    # print_dataset_info(data) # uncomment to see class distributions, etc.
    ts_samples_plot.show()

    # from lets_plot import ggsave

    # ggsave(ts_samples_plot, f"samples_{dataset}.pdf")


2025-03-31 14:16:54.306 |     INFO |         loading | Loading UCR dataset: FordA
2025-03-31 14:16:54.318 |     INFO |         loading | Dataset loaded: train=3601 test=1320 samples
2025-03-31 14:16:54.322 |     INFO |         loading | Found 2 unique classes
2025-03-31 14:16:54.324 |     INFO |         loading | Successfully processed FordA data: 1 features, 500 timesteps


<path d="M13.394645653570212 59.52275219897584 L13.394645653570212 59.52275219897584 L13.931505198803487 66.05536276395873 L14.468364744036762 74.48322385393581 L15.005224289270037 81.6692986011399 L15.542083834503313 84.5192997813982 L16.078943379736586 81.26215557538872 L16.615802924969863 72.67143750357494 L17.152662470203136 61.210360129244215 L17.68952201543641 48.93499727457059 L18.226381560669687 38.30856293168196 L18.763241105902964 32.4049902006087 L19.300100651136237 31.99784489021967 L19.83696019636951 36.27284780292604 L20.373819741602787 43.09249405541784 L20.91067928683606 50.76714089045092 L21.447538832069334 57.309929731218865 L21.98439837730261 62.06536071178549 L22.521257922535888 63.51071856743409 L23.05811746776916 61.515717398557605 L23.594977013002435 57.24478685281027 L24.13183655823571 51.66285543287163 L24.668696103468985 45.637138537522205 L25.20555564870226 41.23999317401805 L25.742415193935535 39.79463531836946 L26.279274739168812 43.112851320937295 L26.816134284402086 50.74678362493147 L27.35299382963536 60.21285968759584 L27.889853374868636 69.92322150859498 L28.42671292010191 77.7810825909842 L28.963572465335183 82.0764416268911 L29.50043201056846 82.48358465264228 L30.037291555801737 79.63358347238398 L30.57415110103501 74.13715262474298 L31.111010646268284 68.78322149341923 L31.64787019150156 65.54643398176974 L32.18472973673484 65.91286247648202 L32.72158928196811 69.90286424307553 L33.258448827201384 75.35858170199654 L33.79530837243466 79.08394073031556 L34.33216791766793 79.8371561275785 L34.869027462901215 75.66393840015047 L35.405887008134485 66.40143399315156 L35.942746553367755 53.902142074503146 L36.47960609860104 41.05677892666192 L37.01646564383431 30.97998846816063 L37.553325189067586 26.09426987450857 L38.09018473430086 27.315698951762123 L38.62704427953413 34.84784835511581 L39.16390382476741 46.227495810629534 L39.700763370000686 57.95525146415986 L40.237622915233956 67.94857760523794 L40.77448246046723 73.91322384634795 L41.31134200570051 75.84715264750662 L41.84820155093378 75.60286774591104 L42.385061096167064 74.50358111945528 L42.921920641400334 75.1753674546404 L43.458780186633604 78.53429570360929 L43.99563973186689 83.09429804895012 L44.53249927710016 86.35144453959745 L45.069358822333434 86.35144453959745 L45.60621836756671 81.26215557538872 L46.14307791279998 70.26929273778781 L46.679937458033265 55.38821446119065 L47.216797003266535 39.48927747789661 L47.753656548499805 25.68712913339523 L48.29051609373309 16.729980282231317 L48.82737563896636 14.490692498280879 L49.36423518419963 18.56212275579273 L49.90109472943291 27.92641463270782 L50.43795427466618 40.05927862780341 L50.97481381989945 52.96571357220299 L51.51167336513274 64.61000490831013 L52.048532910366006 74.40179479185801 L52.585392455599276 82.2800142820856 L53.12225200083256 87.16573059109982 L53.65911154606583 90.2193021419148 L54.195971091299114 90.4228747971093 L54.732830636532384 86.75858756534863 L55.269690181765654 79.8371561275785 L55.80654972699894 70.39143633090453 L56.34340927223221 60.64035997886648 L56.88026881746548 52.55856997529235 L57.41712836269876 48.38535339018324 L57.95398790793203 49.15892605296563 L58.4908474531653 53.617142070709214 L59.027706998398585 59.37821644196895 L59.564566543631855 63.24607554357987 L60.10142608886514 62.41143222655805 L60.63828563409841 56.12107202177468 L61.17514517933168 45.799995519358895 L61.71200472456496 35.86570477717485 L62.24886426979823 29.55498673571256 L62.7857238150315 30.572845442409445 L63.32258336026479 39.30606551517832 L63.85944290549806 54.57392840968828 L64.39630245073133 72.0403656994287 L64.93316199596461 86.14787188440295 L65.47002154119788 93.88358937367545 L66.00688108643115 94.08716202886997 L66.54374063166443 86.96216022054315 L67.0806001768977 75.37893896751599 L67.61745972213099 63.40893281099629 L68.15431926736426 54.614642655147456 L68.69117881259753 51.76464118930943 L69.22803835783081 54.431428407791316 L69.76489790306408 59.90

2025-03-31 14:16:54.702 |     INFO |         loading | Loading UCR dataset: FordB
2025-03-31 14:16:54.714 |     INFO |         loading | Dataset loaded: train=3636 test=810 samples
2025-03-31 14:16:54.718 |     INFO |         loading | Found 2 unique classes
2025-03-31 14:16:54.719 |     INFO |         loading | Successfully processed FordB data: 1 features, 500 timesteps


<path d="M13.394645653570212 89.00431698552855 L13.394645653570212 89.00431698552855 L13.931505198803487 96.83738587115431 L14.468364744036762 97.82889989213191 L15.005224289270037 92.47360527414659 L15.542083834503313 83.65932782968704 L16.078943379736586 74.34106172501215 L16.615802924969863 65.86625806041678 L17.152662470203136 58.946929267625045 L17.68952201543641 53.535354662845364 L18.226381560669687 49.07294531898328 L18.763241105902964 45.81897917922712 L19.300100651136237 43.08372167928142 L19.83696019636951 42.41981323457496 L20.373819741602787 45.03850907525159 L20.91067928683606 51.05677347093194 L21.447538832069334 59.804403339388756 L21.98439837730261 69.54961580616818 L22.521257922535888 77.97964170396338 L23.05811746776916 82.65791038906052 L23.594977013002435 82.25523189471228 L24.13183655823571 77.96733057219801 L24.668696103468985 71.19180153377795 L25.20555564870226 64.06348247749102 L25.742415193935535 57.95965443836383 L26.279274739168812 54.82128303999789 L26.816134284402086 54.32558054374568 L27.35299382963536 55.09985419616107 L27.889853374868636 55.3357617157622 L28.42671292010191 54.19386960526826 L28.963572465335183 52.33629188243097 L29.50043201056846 50.62301845458221 L30.037291555801737 50.38475546567467 L30.57415110103501 53.84795746691904 L31.111010646268284 60.769262045877106 L31.64787019150156 68.72634861932227 L32.18472973673484 75.25616041483644 L32.72158928196811 77.69967929905366 L33.258448827201384 74.18676144974383 L33.79530837243466 65.32186980802817 L34.33216791766793 54.28323831403692 L34.869027462901215 44.61923440299861 L35.405887008134485 39.63423682282141 L35.942746553367755 40.82715596234236 L36.47960609860104 47.63303693770245 L37.01646564383431 58.47182577067124 L37.553325189067586 69.81426993201282 L38.09018473430086 78.14505039065213 L38.62704427953413 81.04745535429144 L39.16390382476741 78.47626867081127 L39.700763370000686 71.05817691845323 L40.237622915233956 60.37562652641729 L40.77448246046723 48.80245703410924 L41.31134200570051 38.46339822054976 L41.84820155093378 30.78449559602736 L42.385061096167064 26.962706896424393 L42.921920641400334 27.35815998299666 L43.458780186633604 31.285270187709845 L43.99563973186689 38.65570400443404 L44.53249927710016 49.464973094355884 L45.069358822333434 63.32872710375721 L45.60621836756671 78.27191637635177 L46.14307791279998 91.97323272495902 L46.679937458033265 102.20472359257508 L47.216797003266535 107.4186968664558 L47.753656548499805 106.61989521471044 L48.29051609373309 100.74361939467641 L48.82737563896636 90.76519042763476 L49.36423518419963 78.65987716253139 L49.90109472943291 66.48756987564369 L50.43795427466618 56.69264463077369 L50.97481381989945 50.06358824788857 L51.51167336513274 45.53807981087584 L52.048532910366006 42.54828625454102 L52.585392455599276 41.35643695691333 L53.12225200083256 41.1154170240611 L53.65911154606583 42.30820328513035 L54.195971091299114 44.70622095319919 L54.732830636532384 47.86300297337087 L55.269690181765654 50.93176721569963 L55.80654972699894 53.78602304771907 L56.34340927223221 55.54965485341156 L56.88026881746548 55.68048277482739 L57.41712836269876 54.61727997736661 L57.95398790793203 53.12275741671918 L58.4908474531653 52.319202237113664 L59.027706998398585 52.43085307223573 L59.564566543631855 54.34862530155485 L60.10142608886514 57.601292611231194 L60.63828563409841 62.874938389385484 L61.17514517933168 68.62296861603427 L61.71200472456496 73.26363326715375 L62.24886426979823 75.9741344894037 L62.7857238150315 75.7388692156525 L63.32258336026479 73.04375804382254 L63.85944290549806 68.07522092381522 L64.39630245073133 62.72354184900102 L64.93316199596461 58.50365484467329 L65.47002154119788 56.22824352774896 L66.00688108643115 55.80573008519966 L66.54374063166443 57.150956607141595 L67.0806001768977 59.63914231316966 L67.61745972213099 61.830216627952716 L68.15431926736426 63.396362519606555 L68.69117881259753 63.188665549589025 L69.22803835783081 61.04403239564321 L69.7648979030

2025-03-31 14:16:55.134 |     INFO |         loading | Loading UCR dataset: Wafer
2025-03-31 14:16:55.137 |     INFO |         loading | Dataset loaded: train=1000 test=6164 samples
2025-03-31 14:16:55.141 |     INFO |         loading | Found 2 unique classes
2025-03-31 14:16:55.143 |     INFO |         loading | Successfully processed Wafer data: 1 features, 152 timesteps


<path d="M13.617879372604289 107.74506271320902 L13.617879372604289 107.74506271320902 L15.421572004737307 112.362033040589 L17.225264636870325 110.59168008910089 L19.028957269003342 111.67450131639204 L20.832649901136364 110.83929508178176 L22.636342533269378 111.62537111509104 L24.4400351654024 110.75050781286637 L26.243727797535417 111.86995837062057 L28.047420429668435 110.25313954429387 L29.851113061801453 112.84973051904366 L31.65480569393447 54.28986377444268 L33.458498326067485 46.08577242340012 L35.262190958200506 48.188951851955615 L37.06588359033353 45.88733255393643 L38.86957622246655 46.7701128946708 L40.67326885459956 45.633196695901105 L42.47696148673258 46.43758649600359 L44.2806541188656 45.37080958029961 L46.08434675099862 46.701702206940155 L47.88803938313164 44.63900640925699 L49.69173201526465 103.58139764524702 L51.49542464739767 112.92050589644266 L53.29911727953069 110.15997149011142 L55.10280991166371 111.68930757996895 L56.906502543796734 110.73089310738024 L58.71019517592974 111.48926669341218 L60.51388780806276 110.96630012011676 L62.31758044019578 111.54308853964027 L64.1212730723288 110.65372264599213 L65.92496570446181 111.8397492804197 L67.72865833659483 110.04481146263797 L69.53235096872785 112.90306181794693 L71.33604360086088 108.46075688510514 L73.1397362329939 116.48323791336621 L74.9434288651269 92.45251579975508 L76.74712149725993 48.053629071618495 L78.55081412939295 56.56784336328492 L80.35450676152597 50.77066468806258 L82.15819939365899 53.377048640542256 L83.961892025792 51.081147004016 L85.76558465792502 52.135248751847215 L87.56927729005804 51.51235786817406 L89.37296992219106 51.84423200061816 L91.17666255432408 51.49253652187345 L92.98035518645709 51.56832338824284 L94.78404781859011 51.590300986520674 L96.58774045072313 51.541283988448484 L98.39143308285615 51.510758647957616 L100.19512571498917 51.5295090557762 L101.99881834712218 51.45492969051406 L103.8025109792552 51.455759847525286 L105.60620361138822 51.52047076623835 L107.40989624352125 51.58132019703554 L109.21358887565425 51.57390089335725 L111.01728150778727 51.52854233613975 L112.8209741399203 51.528375226611516 L114.62466677205332 51.49223644347329 L116.42835940418634 51.452198438009574 L118.23205203631935 51.48137791789132 L120.03574466845237 51.457328520838715 L121.83943730058539 51.46648899798861 L123.64312993271841 51.47124353359838 L125.44682256485142 51.466611185600655 L127.25051519698444 51.46037602363319 L129.05420782911744 51.46699032657331 L130.85790046125047 51.477200179685454 L132.6615930933835 51.44433530579931 L134.4652857255165 51.48957167540477 L136.26897835764953 51.393925728325165 L138.07267098978255 51.51706748186764 L139.87636362191557 51.58799379690504 L141.68005625404857 51.57699691182121 L143.4837488861816 51.507119972746054 L145.2874415183146 51.52901671157474 L147.09113415044763 51.473570488857135 L148.89482678258065 51.46767134282278 L150.69851941471367 51.45686133291032 L152.5022120468467 51.46886446891685 L154.3059046789797 51.471994628037116 L156.1095973111127 51.459786648092745 L157.91328994324573 51.46594813811765 L159.71698257537875 51.472578612947615 L161.52067520751177 51.46472266824394 L163.3243678396448 51.46134993077624 L165.12806047177781 51.472111425019214 L166.93175310391084 51.46862009369276 L168.73544573604386 51.455714925609094 L170.53913836817685 51.47026243894875 L172.34283100030987 51.471218377325314 L174.1465236324429 51.45823774042245 L175.95021626457591 51.426116773468436 L177.75390889670894 51.49245386554765 L179.55760152884196 51.35837093009743 L181.36129416097498 51.59270520747528 L183.164986793108 51.21461361077607 L184.96867942524102 51.80451922982768 L186.77237205737404 50.88498916789487 L188.57606468950704 52.36356349245531 L190.37975732164006 49.70325886553192 L192.18344995377308 56.91132352199642 L193.9871425859061 112.4489479640375 L195.79083521803912 110.43159634855866 L197.59452785017214 111.7092924420445 L199.39822048230516 110.89411419454932 L201.20191311

2025-03-31 14:16:55.194 |     INFO |         loading | Loading UCR dataset: ElectricDevices
2025-03-31 14:16:55.203 |     INFO |         loading | Dataset loaded: train=8926 test=7711 samples
2025-03-31 14:16:55.209 |     INFO |         loading | Found 7 unique classes
2025-03-31 14:16:55.211 |     INFO |         loading | Successfully processed ElectricDevices data: 1 features, 96 timesteps


<path d="M13.617879372604287 148.68633338149272 L13.617879372604287 148.68633338149272 L16.48480134578414 148.68633338149272 L19.351723318963987 148.68633338149272 L22.21864529214384 148.68633338149272 L25.08556726532369 148.68633338149272 L27.95248923850354 148.68633338149272 L30.819411211683388 148.68633338149272 L33.68633318486324 148.68633338149272 L36.553255158043086 148.68633338149272 L39.420177131222935 148.68633338149272 L42.287099104402785 148.68633338149272 L45.15402107758264 148.68633338149272 L48.02094305076249 148.68633338149272 L50.88786502394234 148.68633338149272 L53.75478699712219 148.68633338149272 L56.62170897030204 148.68633338149272 L59.48863094348189 148.68633338149272 L62.355552916661736 148.68633338149272 L65.22247488984159 148.68633338149272 L68.08939686302143 148.68633338149272 L70.95631883620129 148.68633338149272 L73.82324080938115 148.68633338149272 L76.69016278256099 148.68633338149272 L79.55708475574085 148.68633338149272 L82.4240067289207 148.68633338149272 L85.29092870210054 148.68633338149272 L88.1578506752804 148.68633338149272 L91.02477264846024 148.68633338149272 L93.8916946216401 148.68633338149272 L96.75861659481994 148.68633338149272 L99.6255385679998 148.68633338149272 L102.49246054117964 148.68633338149272 L105.3593825143595 148.68633338149272 L108.22630448753935 148.68633338149272 L111.0932264607192 148.68633338149272 L113.96014843389905 148.68633338149272 L116.82707040707889 148.68633338149272 L119.69399238025875 148.68633338149272 L122.56091435343859 148.68633338149272 L125.42783632661845 148.68633338149272 L128.29475829979827 148.68633338149272 L131.16168027297815 148.68633338149272 L134.028602246158 148.68633338149272 L136.89552421933783 148.68633338149272 L139.7624461925177 148.68633338149272 L142.62936816569754 148.68633338149272 L145.49629013887738 148.68633338149272 L148.36321211205723 148.68633338149272 L151.2301340852371 148.68633338149272 L154.09705605841694 148.68633338149272 L156.96397803159678 148.68633338149272 L159.83090000477662 148.68633338149272 L162.6978219779565 71.85434472160505 L165.56474395113634 68.6323621645606 L168.43166592431618 78.05047675887012 L171.29858789749602 134.06347137029104 L174.1655098706759 144.72081142500647 L177.03243184385573 144.9686565331939 L179.89935381703557 38.395258933482026 L182.76627579021545 136.54192274207767 L185.6331977633953 148.68633338149272 L188.50011973657513 148.68633338149272 L191.36704170975497 148.68633338149272 L194.23396368293484 148.68633338149272 L197.10088565611468 148.68633338149272 L199.96780762929453 148.68633338149272 L202.8347296024744 148.68633338149272 L205.70165157565424 148.68633338149272 L208.56857354883408 148.68633338149272 L211.43549552201392 148.68633338149272 L214.3024174951938 148.68633338149272 L217.16933946837364 148.68633338149272 L220.03626144155348 148.68633338149272 L222.90318341473335 148.68633338149272 L225.7701053879132 148.68633338149272 L228.63702736109303 148.68633338149272 L231.50394933427287 148.68633338149272 L234.37087130745275 148.68633338149272 L237.2377932806326 148.68633338149272 L240.10471525381243 148.68633338149272 L242.97163722699227 148.68633338149272 L245.83855920017214 148.68633338149272 L248.70548117335198 148.68633338149272 L251.57240314653183 148.68633338149272 L254.4393251197117 148.68633338149272 L257.30624709289157 148.68633338149272 L260.1731690660714 148.68633338149272 L263.04009103925125 148.68633338149272 L265.9070130124311 148.68633338149272 L268.77393498561094 148.68633338149272 L271.64085695879083 148.68633338149272 L274.5077789319707 148.68633338149272 L277.3747009051505 148.68633338149272 L280.24162287833036 148.68633338149272 L283.1085448515102 148.68633338149272 L285.97546682469005 148.68633338149272 " fill="none" stroke-width="2.2" stroke="rgb(0,114,178)" stroke-opacity="1.0">
 
 
 
 <path d="M13.617879372604287 148.73622047244095 L13.617879372604287 148.73622047244095 L16.48480134578414 148.73622047244095 L19.351723318963987 148.73622047244095 L22.218645